In [1]:
'''# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session'''

'# This Python 3 environment comes with many helpful analytics libraries installed\n# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python\n# For example, here\'s several helpful packages to load\n\nimport numpy as np # linear algebra\nimport pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)\n\n# Input data files are available in the read-only "../input/" directory\n# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory\n\nimport os\nfor dirname, _, filenames in os.walk(\'/kaggle/input\'):\n    for filename in filenames:\n        print(os.path.join(dirname, filename))\n\n# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" \n# You can also write temporary files to /kaggle/temp/, but they won\'t be saved outside of the current session'

## Importing the training text dataset

In [2]:
import pandas as pd
train_text=pd.read_csv('/kaggle/input/visual-taxonomy/train.csv')
train_text.head()

id     Category  len      attr_1 attr_2   attr_3   attr_4         attr_5  \
0   0  Men Tshirts    5     default  round  printed  default  short sleeves   
1   1  Men Tshirts    5  multicolor   polo    solid    solid  short sleeves   
2   2  Men Tshirts    5     default   polo    solid    solid  short sleeves   
3   3  Men Tshirts    5  multicolor   polo    solid    solid  short sleeves   
4   4  Men Tshirts    5  multicolor   polo    solid    solid  short sleeves   

  attr_6 attr_7 attr_8 attr_9 attr_10  
0    NaN    NaN    NaN    NaN     NaN  
1    NaN    NaN    NaN    NaN     NaN  
2    NaN    NaN    NaN    NaN     NaN  
3    NaN    NaN    NaN    NaN     NaN  
4    NaN    NaN    NaN    NaN     NaN

In [3]:
train_text.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 70213 entries, 0 to 70212
Data columns (total 13 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   id        70213 non-null  int64 
 1   Category  70213 non-null  object
 2   len       70213 non-null  int64 
 3   attr_1    51867 non-null  object
 4   attr_2    55192 non-null  object
 5   attr_3    54698 non-null  object
 6   attr_4    59888 non-null  object
 7   attr_5    56493 non-null  object
 8   attr_6    38116 non-null  object
 9   attr_7    41415 non-null  object
 10  attr_8    37474 non-null  object
 11  attr_9    33565 non-null  object
 12  attr_10   24999 non-null  object
dtypes: int64(2), object(11)
memory usage: 7.0+ MB


## Importing the category attributes file

In [4]:
categort_attr=pd.read_parquet('/kaggle/input/visual-taxonomy/category_attributes.parquet', engine='pyarrow')
categort_attr

Category  No_of_attribute  \
0          Men Tshirts                5   
1               Sarees               10   
2               Kurtis                9   
3        Women Tshirts                8   
4  Women Tops & Tunics               10   

                                      Attribute_list  
0  [color, neck, pattern, print_or_pattern_type, ...  
1  [blouse_pattern, border, border_width, color, ...  
2  [color, fit_shape, length, occasion, ornamenta...  
3  [color, fit_shape, length, pattern, print_or_p...  
4  [color, fit_shape, length, neck_collar, ocassi...

In [5]:
category_len={'Men Tshirts':5,'Sarees':10,'Kurtis':9,'Women Tshirts':8,'Women Tops & Tunics':10}

## Importing the test dataset

In [6]:
test_text=pd.read_csv('/kaggle/input/visual-taxonomy/test.csv')
test_text.head()

id     Category
0   0  Men Tshirts
1   1  Men Tshirts
2   2  Men Tshirts
3   3  Men Tshirts
4   4  Men Tshirts

## Working on the image data before modelling

### Importing Vision Transformer (ViT) from huggingface

In [7]:
from transformers import TFAutoModel, ViTFeatureExtractor

# Load the ViT feature extractor and model
vit_extractor = ViTFeatureExtractor.from_pretrained('google/vit-base-patch16-224-in21k')
vit_model = TFAutoModel.from_pretrained('google/vit-base-patch16-224-in21k')

preprocessor_config.json:   0%|          | 0.00/160 [00:00<?, ?B/s]

/opt/conda/lib/python3.10/site-packages/transformers/models/vit/feature_extraction_vit.py:28: FutureWarning: The class ViTFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use ViTImageProcessor instead.
  warnings.warn(


config.json:   0%|          | 0.00/502 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/346M [00:00<?, ?B/s]

All PyTorch model weights were used when initializing TFViTModel.

All the weights of TFViTModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFViTModel for predictions without further training.


The vit_extractor is an instance of ViTFeatureExtractor from the HuggingFace transformers library. It is designed to preprocess the images into a format that is suitable for the pre-trained Vision Transformer model.

### Importing the training images and preprocessing them to give them as input to ViT Extractor (Image Preprocessing & Feature Extraction)

In [ ]:
import tensorflow as tf
import os
import numpy as np

def process_image(image_path):
    image = tf.io.read_file(image_path)
    image = tf.image.decode_jpeg(image, channels=3)
    # Normalize
    image = tf.cast(image, tf.float32)
    image = image / 255.0
    image = tf.image.resize(image, [224, 224])
    image = vit_extractor(images=image.numpy(), return_tensors="tf")['pixel_values']
    return image

image_features = []
count=0
folder_path='/kaggle/input/visual-taxonomy/train_images'
for filename in os.listdir(folder_path):
    if filename.endswith(".jpg"):  
        count+=1
        if count>1000: break
        img_path = os.path.join(folder_path, filename)
        # Preprocess image
        image_tensor = process_image(img_path) 
        
        # Extract image features using ViT
        with tf.device('/GPU:0'):  # Using GPU
            outputs = vit_model(image_tensor)
        
        # Extract the CLS token embeddings (representing the entire image)
        cls_embedding = outputs.last_hidden_state[:, 0, :]  # CLS token
        
        # Append the features to the list
        image_features.append(cls_embedding.numpy())

# Convert the list of features to a NumPy array for modeling
image_features = np.array(image_features)
print(image_features.shape)  # Check the shape of the feature array

What is the CLS Token?
In the Vision Transformer (ViT) architecture, an image is split into patches, and these patches are treated as tokens that are fed into the transformer.
A special token, known as the [CLS] token (classification token), is prepended to the sequence of image patch tokens.
As the image passes through the transformer layers, the CLS token aggregates information from all the other tokens (patches). By the end of the model, the CLS token contains a global representation of the entire image.

## Training a combined model 

In [ ]:
import tensorflow as tf
from tensorflow.keras.layers import Dense, Input, Concatenate
from tensorflow.keras.models import Model

# Image model (ViT embeddings already extracted)
image_input = Input(shape=(image_features.shape[1],), name='image_input')
x_image = Dense(128, activation='relu')(image_input)

# Tabular model
tabular_input = Input(shape=(tabular_features.shape[1],), name='tabular_input')
x_tabular = Dense(128, activation='relu')(tabular_input)

In [ ]:
# Calculate number of unique classes for each attribute
num_attr_1_classes = train_text['attr_1'].nunique()
num_attr_2_classes = train_text['attr_2'].nunique()
num_attr_3_classes = train_text['attr_3'].nunique()
num_attr_4_classes = train_text['attr_4'].nunique()
num_attr_5_classes = train_text['attr_5'].nunique()
num_attr_6_classes = train_text['attr_6'].nunique()
num_attr_7_classes = train_text['attr_7'].nunique()
num_attr_8_classes = train_text['attr_8'].nunique()
num_attr_9_classes = train_text['attr_9'].nunique()
num_attr_10_classes = train_text['attr_10'].nunique()

In [ ]:
# Function to encode labels and save the encoder for reversing later
def encode_labels(column):
    label_encoder = LabelEncoder()
    integer_encoded = label_encoder.fit_transform(train_text[column].fillna('dummy_value'))  # Fill NaNs with 'dummy_value'
    onehot_encoded = to_categorical(integer_encoded)  # Convert to one-hot encoding
    return onehot_encoded, label_encoder  # Return both the encoded labels and the encoder

# One-hot encoding the labels for each attribute and storing encoders
attr_1_labels, encoder_attr_1 = encode_labels('attr_1')
attr_2_labels, encoder_attr_2 = encode_labels('attr_2')
attr_3_labels, encoder_attr_3 = encode_labels('attr_3')
attr_4_labels, encoder_attr_4 = encode_labels('attr_4')
attr_5_labels, encoder_attr_5 = encode_labels('attr_5')
attr_6_labels, encoder_attr_6 = encode_labels('attr_6')
attr_7_labels, encoder_attr_7 = encode_labels('attr_7')
attr_8_labels, encoder_attr_8 = encode_labels('attr_8')
attr_9_labels, encoder_attr_9 = encode_labels('attr_9')
attr_10_labels, encoder_attr_10 = encode_labels('attr_10')

In [ ]:
# Flatten the image features to (32, 768) for each sample
image_features = image_features.reshape((image_features.shape[0], -1))

# Redefine the model with correct input shape
from tensorflow.keras.layers import Input, Dense, Concatenate, Flatten
from tensorflow.keras.models import Model

# Input layers
image_input = Input(shape=(768,), name='image_input')  # For ViT features
tabular_input = Input(shape=(2,), name='tabular_input')  # For tabular data (2 features)

# Dense layers for image features
x1 = Dense(128, activation='relu')(image_input)

# Dense layers for tabular features
x2 = Dense(128, activation='relu')(tabular_input)

# Concatenate image and tabular inputs
x = Concatenate()([x1, x2])

# Further dense layers after concatenation
x = Dense(128, activation='relu')(x)

# Output layers for attributes
output_1 = Dense(num_attr_1_classes, activation='softmax', name='attr_1')(x)
output_2 = Dense(num_attr_2_classes, activation='softmax', name='attr_2')(x)
output_3 = Dense(num_attr_3_classes, activation='softmax', name='attr_3')(x)
output_4 = Dense(num_attr_4_classes, activation='softmax', name='attr_4')(x)
output_5 = Dense(num_attr_5_classes, activation='softmax', name='attr_5')(x)
output_6 = Dense(num_attr_6_classes, activation='softmax', name='attr_6')(x)
output_7 = Dense(num_attr_7_classes, activation='softmax', name='attr_7')(x)
output_8 = Dense(num_attr_8_classes, activation='softmax', name='attr_8')(x)
output_9 = Dense(num_attr_9_classes, activation='softmax', name='attr_9')(x)
output_10 = Dense(num_attr_10_classes, activation='softmax', name='attr_10')(x)

# Build the model
model = Model(inputs=[image_input, tabular_input], 
              outputs=[output_1, output_2, output_3, output_4, output_5, 
                       output_6, output_7, output_8, output_9, output_10])

# Compile the model
model.compile(optimizer='adam', 
              loss={'attr_1': 'categorical_crossentropy',
                    'attr_2': 'categorical_crossentropy',
                    'attr_3': 'categorical_crossentropy',
                    'attr_4': 'categorical_crossentropy',
                    'attr_5': 'categorical_crossentropy',
                    'attr_6': 'categorical_crossentropy',
                    'attr_7': 'categorical_crossentropy',
                    'attr_8': 'categorical_crossentropy',
                    'attr_9': 'categorical_crossentropy',
                    'attr_10': 'categorical_crossentropy'},
              metrics={'attr_1': 'accuracy',
                       'attr_2': 'accuracy',
                       'attr_3': 'accuracy',
                       'attr_4': 'accuracy',
                       'attr_5': 'accuracy',
                       'attr_6': 'accuracy',
                       'attr_7': 'accuracy',
                       'attr_8': 'accuracy',
                       'attr_9': 'accuracy',
                       'attr_10': 'accuracy'})  # Metrics for each output

# Train the model
history = model.fit([image_features, tabular_features[:,:2]], 
                    [attr_1_labels, attr_2_labels, attr_3_labels, 
                     attr_4_labels, attr_5_labels, attr_6_labels, 
                     attr_7_labels, attr_8_labels, attr_9_labels, 
                     attr_10_labels],
                    epochs=50, batch_size=32, validation_split=0.2)

In [ ]:
import torch

# Save function to save model checkpoint
def save_checkpoint(epoch, model, optimizer, filepath='checkpoint.pth'):
    torch.save({
        'epoch': epoch,
        'model_state_dict': model.state_dict(),
        'optimizer_state_dict': optimizer.state_dict(),
    }, filepath)

In [ ]:
# Loading the checkpoint
def load_checkpoint(filepath='checkpoint.pth'):
    checkpoint = torch.load(filepath)
    model.load_state_dict(checkpoint['model_state_dict'])
    optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
    epoch = checkpoint['epoch']
    return epoch

In [ ]:
# During training, save checkpoint at desired intervals (e.g., every epoch)
save_checkpoint(10, model, optimizer, 'checkpoint_epoch_{epoch}.pth')

## Test the model

In [ ]:
test_features=[]
folder_path='/kaggle/input/visual-taxonomy/test_images'
for filename in os.listdir(folder_path):
    if filename.endswith(".jpg"): 
        img_path = os.path.join(folder_path, filename)
        # Preprocess image
        image_tensor = process_image(img_path) 
        
        # Extract image features using ViT
        with tf.device('/GPU:0'):  # Using GPU
            outputs = vit_model(image_tensor)
        
        # Extract the CLS token embeddings (representing the entire image)
        cls_embedding = outputs.last_hidden_state[:, 0, :]  # CLS token
        
        # Append the features to the list
        test_features.append(cls_embedding.numpy())

In [ ]:
# Convert the list of features to a NumPy array for testing
test_features = np.array(test_features)
len(test_features)

In [32]:
import pandas as pd
from sklearn.preprocessing import LabelEncoder, StandardScaler

# Encode categorical columns
categorical_columns = test_text.select_dtypes(include=['object']).columns
label_encoder = LabelEncoder()
for i in categorical_columns:
    test_text[i] = label_encoder.fit_transform(test_text[i])

#No need to normalize the length column
'''# Normalize numerical columns
numerical_columns = ['attr_1', 'attr_2', ..., 'attr_10']
scaler = StandardScaler()
train_df[numerical_columns] = scaler.fit_transform(train_df[numerical_columns])'''

# Convert to numpy arrays
test_tabular_features = test_text[:6167].values

### Get predictions

In [33]:
# Reshape the test_features to match the expected input shape
test_features = test_features.reshape(test_features.shape[0], test_features.shape[2])

# Get predictions from the trained model
predictions = model.predict([test_features, test_tabular_features])

193/193 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step


In [34]:
print("Shape of test_tabular_features:", test_tabular_features.shape)

Shape of test_tabular_features: (6167, 2)


In [36]:
# Extract the class with the highest probability for each attribute prediction
predicted_labels = []
for i, prediction in enumerate(predictions):
    predicted_labels.append(np.argmax(prediction, axis=1))

# Display the predicted labels for each attribute
for i, label in enumerate(predicted_labels):
    print(f"Predicted Labels for Attribute {i+1}: {label}")


Predicted Labels for Attribute 1: [6 6 6 ... 6 6 6]
Predicted Labels for Attribute 2: [14 14 14 ...  8  8  8]
Predicted Labels for Attribute 3: [ 9  9  9 ... 10 10 10]
Predicted Labels for Attribute 4: [11 11 11 ... 11 11 11]
Predicted Labels for Attribute 5: [9 9 9 ... 9 9 9]
Predicted Labels for Attribute 6: [7 7 7 ... 7 7 7]
Predicted Labels for Attribute 7: [11 11 11 ... 11 11 11]
Predicted Labels for Attribute 8: [10 10 10 ... 10 10 10]
Predicted Labels for Attribute 9: [13 13 13 ... 13 13 13]
Predicted Labels for Attribute 10: [8 8 8 ... 8 8 8]


## Submission 

In [ ]:
import pandas as pd
import numpy as np

# Number of test samples
total_test_samples = 30205  # Total number of test rows
predicted_samples = 6167    # Number of predicted samples

# Create a DataFrame with NaN for all rows initially
submission_df = pd.DataFrame(np.nan, index=range(total_test_samples), columns=['id','Category','len',
    'Attribute_1', 'Attribute_2', 'Attribute_3', 'Attribute_4', 'Attribute_5', 
    'Attribute_6', 'Attribute_7', 'Attribute_8', 'Attribute_9', 'Attribute_10'
])


In [77]:
submission_df.shape

(30488, 13)

In [78]:
test_text.shape

(30205, 2)

In [79]:
submission_df.iloc[:30205,0] = test_text.iloc[:,0]
submission_df.iloc[:30205,1] = test_text.iloc[:,1]

In [69]:
for i in range(predicted_samples):
    submission_df['len'][i] = category_len[submission_df['Category'][i]]

/tmp/ipykernel_30/481981211.py:15: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '['Men Tshirts' 'Men Tshirts' 'Men Tshirts' ... 'Sarees' 'Sarees' 'Sarees']' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  submission_df.iloc[:predicted_samples,1] = test_text['Category'][:predicted_samples]
/tmp/ipykernel_30/481981211.py:18: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"]

## Reversing the encoding

In [70]:
# Reverse the encoding of predicted labels using LabelEncoder's inverse_transform
reversed_attr_1 = encoder_attr_1.inverse_transform(predicted_labels[0])  # For Attribute 1
reversed_attr_2 = encoder_attr_2.inverse_transform(predicted_labels[1])  # For Attribute 2
reversed_attr_3 = encoder_attr_3.inverse_transform(predicted_labels[2])  # For Attribute 3
reversed_attr_4 = encoder_attr_4.inverse_transform(predicted_labels[3])  # For Attribute 4
reversed_attr_5 = encoder_attr_5.inverse_transform(predicted_labels[4])  # For Attribute 5
reversed_attr_6 = encoder_attr_6.inverse_transform(predicted_labels[5])  # For Attribute 6
reversed_attr_7 = encoder_attr_7.inverse_transform(predicted_labels[6])  # For Attribute 7
reversed_attr_8 = encoder_attr_8.inverse_transform(predicted_labels[7])  # For Attribute 8
reversed_attr_9 = encoder_attr_9.inverse_transform(predicted_labels[8])  # For Attribute 9
reversed_attr_10 = encoder_attr_10.inverse_transform(predicted_labels[9])  # For Attribute 10


In [71]:
# Prepare the submission DataFrame
submission_df.iloc[:predicted_samples, 3] = reversed_attr_1
submission_df.iloc[:predicted_samples, 4] = reversed_attr_2
submission_df.iloc[:predicted_samples, 5] = reversed_attr_3
submission_df.iloc[:predicted_samples, 6] = reversed_attr_4
submission_df.iloc[:predicted_samples, 7] = reversed_attr_5
submission_df.iloc[:predicted_samples, 8] = reversed_attr_6
submission_df.iloc[:predicted_samples, 9] = reversed_attr_7
submission_df.iloc[:predicted_samples, 10] = reversed_attr_8
submission_df.iloc[:predicted_samples, 11] = reversed_attr_9
submission_df.iloc[:predicted_samples, 12] = reversed_attr_10

# Fill the remaining rows with NaN
submission_df.iloc[predicted_samples:] = np.nan

/tmp/ipykernel_30/2001768510.py:2: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '['maroon' 'maroon' 'maroon' ... 'maroon' 'maroon' 'maroon']' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  submission_df.iloc[:predicted_samples, 3] = reversed_attr_1
/tmp/ipykernel_30/2001768510.py:3: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '['zari' 'zari' 'zari' ... 'regular' 'regular' 'regular']' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  submission_df.iloc[:predicted_samples, 4] = reversed_attr_2
/tmp/ipykernel_30/2001768510.py:4: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '['small border' 'small border' 'small border' ... 'solid' 'solid' 'solid']' has dtype i

In [81]:
submission_df=submission_df.iloc[:30205,:]

In [82]:
submission_df

id             Category  len Attribute_1 Attribute_2  \
0          0.0          Men Tshirts  5.0      maroon        zari   
1          1.0          Men Tshirts  5.0      maroon        zari   
2          2.0          Men Tshirts  5.0      maroon        zari   
3          3.0          Men Tshirts  5.0      maroon   no border   
4          4.0          Men Tshirts  5.0      maroon   no border   
...        ...                  ...  ...         ...         ...   
30200  30484.0  Women Tops & Tunics  NaN         NaN         NaN   
30201  30485.0  Women Tops & Tunics  NaN         NaN         NaN   
30202  30486.0  Women Tops & Tunics  NaN         NaN         NaN   
30203  30487.0  Women Tops & Tunics  NaN         NaN         NaN   
30204  30488.0  Women Tops & Tunics  NaN         NaN         NaN   

        Attribute_3 Attribute_4 Attribute_5          Attribute_6 Attribute_7  \
0      small border  round neck      quirky  tassels and latkans  zari woven   
1      small border  round neck      quirky  tassels and latkans  zari woven   
2      small border  round neck      quirky  tassels and latkans  zari woven   
3      small border  round neck      quirky  tassels and latkans  zari woven   
4      small border  round neck      quirky  tassels and latkans  zari woven   
...             ...         ...         ...                  ...         ...   
30200           NaN         NaN         NaN                  NaN         NaN   
30201           NaN         NaN         NaN                  NaN         NaN   
30202           NaN         NaN         NaN                  NaN         NaN   
30203           NaN         NaN         NaN                  NaN         NaN   
30204           NaN         NaN         NaN                  NaN         NaN   

      Attribute_8 Attribute_9 Attribute_10  
0      zari woven       solid          yes  
1      zari woven       solid          yes  
2      zari woven       solid          yes  
3      zari woven       solid          yes  
4      zari woven       solid          yes  
...           ...         ...          ...  
30200         NaN         NaN          NaN  
30201         NaN         NaN          NaN  
30202         NaN         NaN          NaN  
30203         NaN         NaN          NaN  
30204         NaN         NaN          NaN  

[30205 rows x 13 columns]

In [89]:
submission_df.fillna('nu', inplace=True)
        

/tmp/ipykernel_30/3818306898.py:1: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value 'nu' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  submission_df.fillna('nu', inplace=True)
/tmp/ipykernel_30/3818306898.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  submission_df.fillna('nu', inplace=True)


In [93]:
# Rename columns
submission_df.rename(columns={
    'Attribute_1': 'attr_1',
    'Attribute_2': 'attr_2',
    'Attribute_3': 'attr_3',
    'Attribute_4': 'attr_4',
    'Attribute_5': 'attr_5',
    'Attribute_6': 'attr_6',
    'Attribute_7': 'attr_7',
    'Attribute_8': 'attr_8',
    'Attribute_9': 'attr_9',
    'Attribute_10': 'attr_10',
}, inplace=True)

/tmp/ipykernel_30/3823126089.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  submission_df.rename(columns={


In [94]:
submission_df

id             Category  len  attr_1     attr_2        attr_3  \
0          0.0          Men Tshirts  5.0  maroon       zari  small border   
1          1.0          Men Tshirts  5.0  maroon       zari  small border   
2          2.0          Men Tshirts  5.0  maroon       zari  small border   
3          3.0          Men Tshirts  5.0  maroon  no border  small border   
4          4.0          Men Tshirts  5.0  maroon  no border  small border   
...        ...                  ...  ...     ...        ...           ...   
30200  30484.0  Women Tops & Tunics   nu      nu         nu            nu   
30201  30485.0  Women Tops & Tunics   nu      nu         nu            nu   
30202  30486.0  Women Tops & Tunics   nu      nu         nu            nu   
30203  30487.0  Women Tops & Tunics   nu      nu         nu            nu   
30204  30488.0  Women Tops & Tunics   nu      nu         nu            nu   

           attr_4  attr_5               attr_6      attr_7      attr_8 attr_9  \
0      round neck  quirky  tassels and latkans  zari woven  zari woven  solid   
1      round neck  quirky  tassels and latkans  zari woven  zari woven  solid   
2      round neck  quirky  tassels and latkans  zari woven  zari woven  solid   
3      round neck  quirky  tassels and latkans  zari woven  zari woven  solid   
4      round neck  quirky  tassels and latkans  zari woven  zari woven  solid   
...           ...     ...                  ...         ...         ...    ...   
30200          nu      nu                   nu          nu          nu     nu   
30201          nu      nu                   nu          nu          nu     nu   
30202          nu      nu                   nu          nu          nu     nu   
30203          nu      nu                   nu          nu          nu     nu   
30204          nu      nu                   nu          nu          nu     nu   

      attr_10  
0         yes  
1         yes  
2         yes  
3         yes  
4         yes  
...       ...  
30200      nu  
30201      nu  
30202      nu  
30203      nu  
30204      nu  

[30205 rows x 13 columns]

In [95]:
# Save the DataFrame to a CSV file
submission_file = 'submission.csv'
submission_df.to_csv(submission_file, index=False)

print("Submission file created successfully!")


Submission file created successfully!
